In [14]:
spark.stop()

In [13]:
from pyspark.sql import SparkSession

# Tạo SparkSession
spark = SparkSession.builder \
    .appName("RealEstateJSONQuery2") \
    .master("spark://spark-master:7077") \
    .config("spark.hadoop.fs.defaultFS", "hdfs://namenode:9000") \
    .getOrCreate()

# Đường dẫn trên HDFS
json_path = "hdfs://namenode:9000/data/realestate/raw/chotot/house/2025/05/*"

# Đọc dữ liệu JSON từ HDFS
df = spark.read.option("multiline", "false").json(json_path)

# Hiển thị schema
df.printSchema()

# Xem trước dữ liệu
selected_cols = ["price", "price_per_m2", "area", "bedroom", "bathroom", "location", "posted_date"]
selected_df = df.select(selected_cols)

selected_df.show(5)
# Ví dụ: Truy vấn nhà giá > 3 tỷ
# df.filter(df.price > 3_000_000_000).select("title", "price", "location").show()


25/05/24 16:40:01 WARN Utils: Service 'SparkUI' could not bind on port 4040. Attempting port 4041.
ERROR:root:Exception while sending command.                         (0 + 2) / 2]
Traceback (most recent call last):
  File "/opt/conda/lib/python3.11/site-packages/py4j/clientserver.py", line 511, in send_command
    answer = smart_decode(self.stream.readline()[:-1])
                          ^^^^^^^^^^^^^^^^^^^^^^
RuntimeError: reentrant call inside <_io.BufferedReader name=60>

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/opt/conda/lib/python3.11/site-packages/py4j/java_gateway.py", line 1038, in send_command
    response = connection.send_command(command)
               ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/opt/conda/lib/python3.11/site-packages/py4j/clientserver.py", line 539, in send_command
    raise Py4JNetworkError(
py4j.protocol.Py4JNetworkError: Error while sending or receiving
ERROR:root:Exception while sen

Py4JError: An error occurred while calling o150.json

In [24]:
from pyspark.sql.functions import col, regexp_replace, translate, when, lit, min as min_f, max as max_f, avg as avg_f

# Hiển thị một số mẫu giá ban đầu
print("Dạng giá ban đầu:")
df.select("price").show(10, False)

# Chuyển đổi cột price từ string format "X,Y tỷ" hoặc "Z triệu" thành số
df_clean = df.withColumn(
    "price_cleaned",
    when(
        col("price").contains("tỷ"),
        # Xử lý giá tỷ: chuyển "X,Y tỷ" -> X.Y * 1,000,000,000
        regexp_replace(col("price"), " tỷ", "") # Loại bỏ từ "tỷ"
        .cast("string") # Đảm bảo là string
    )
    .when(
        col("price").contains("triệu"),
        # Xử lý giá triệu: "Z triệu" -> Z * 1,000,000
        regexp_replace(col("price"), " triệu", "") # Loại bỏ từ "triệu"
        .cast("string") # Đảm bảo là string
    )
    .otherwise(col("price")) # Giữ nguyên giá trị nếu không chứa "tỷ" hoặc "triệu"
)

# Thay thế dấu phẩy bằng dấu chấm để chuẩn bị chuyển đổi sang số
df_clean = df_clean.withColumn(
    "price_cleaned", 
    translate(col("price_cleaned"), ",", ".").cast("double")
)

# Chuyển đổi thành giá trị số (VND)
df_clean = df_clean.withColumn(
    "price_vnd", 
    when(col("price").contains("tỷ"), col("price_cleaned") * 1000000000)
    .when(col("price").contains("triệu"), col("price_cleaned") * 1000000)
    .otherwise(col("price_cleaned"))
)

# Hiển thị kết quả
print("\nKết quả sau khi chuyển đổi:")
df_clean.select("price", "price_cleaned", "price_vnd").show(10, False)

# Hiển thị thống kê về giá sau khi chuyển đổi
print("\nThống kê về giá bất động sản (đơn vị: VND):")
df_clean.select(
    min_f(col("price_vnd")).alias("Giá thấp nhất"),
    max_f(col("price_vnd")).alias("Giá cao nhất"), 
    avg_f(col("price_vnd")).alias("Giá trung bình")
).show()

# Phân loại giá theo khoảng (tỷ VND)
print("\nPhân phối giá bất động sản:")
price_ranges = df_clean.select(
    when(col("price_vnd") < 1000000000, "Dưới 1 tỷ")
    .when(col("price_vnd") < 2000000000, "1-2 tỷ")
    .when(col("price_vnd") < 5000000000, "2-5 tỷ")
    .when(col("price_vnd") < 10000000000, "5-10 tỷ")
    .when(col("price_vnd") < 20000000000, "10-20 tỷ")
    .when(col("price_vnd") >= 20000000000, "Trên 20 tỷ")
    .otherwise("Không xác định").alias("Khoảng giá")
)

price_distribution = price_ranges.groupBy("Khoảng giá").count().orderBy("Khoảng giá")
price_distribution.show(truncate=False)

Dạng giá ban đầu:
+-------+
|price  |
+-------+
|8,8 tỷ |
|17,5 tỷ|
|2,6 tỷ |
|7,9 tỷ |
|9,5 tỷ |
|6,8 tỷ |
|16,2 tỷ|
|7 tỷ   |
|1,85 tỷ|
|8 tỷ   |
+-------+
only showing top 10 rows


Kết quả sau khi chuyển đổi:
+-------+-------------+---------+
|price  |price_cleaned|price_vnd|
+-------+-------------+---------+
|8,8 tỷ |8.8          |8.8E9    |
|17,5 tỷ|17.5         |1.75E10  |
|2,6 tỷ |2.6          |2.6E9    |
|7,9 tỷ |7.9          |7.9E9    |
|9,5 tỷ |9.5          |9.5E9    |
|6,8 tỷ |6.8          |6.8E9    |
|16,2 tỷ|16.2         |1.62E10  |
|7 tỷ   |7.0          |7.0E9    |
|1,85 tỷ|1.85         |1.85E9   |
|8 tỷ   |8.0          |8.0E9    |
+-------+-------------+---------+
only showing top 10 rows


Thống kê về giá bất động sản (đơn vị: VND):
+-------------+------------+-------------------+
|Giá thấp nhất|Giá cao nhất|     Giá trung bình|
+-------------+------------+-------------------+
|    2000000.0|      7.0E11|8.008485353543362E9|
+-------------+------------+----------------

In [29]:
from pyspark.sql.functions import col, regexp_replace, translate, when, lit, min as min_f

# Xử lý cột giá
df_clean = df.withColumn(
    "price_cleaned",
    when(
        col("price").contains("tỷ"),
        regexp_replace(col("price"), " tỷ", "").cast("string")
    )
    .when(
        col("price").contains("triệu"),
        regexp_replace(col("price"), " triệu", "").cast("string")
    )
    .otherwise(col("price"))
)

# Thay thế dấu phẩy thành dấu chấm và chuyển sang số
df_clean = df_clean.withColumn(
    "price_cleaned", 
    translate(col("price_cleaned"), ",", ".").cast("double")
)

# Chuyển đổi thành giá trị VND
df_clean = df_clean.withColumn(
    "price_vnd", 
    when(col("price").contains("tỷ"), col("price_cleaned") * 1000000000)
    .when(col("price").contains("triệu"), col("price_cleaned") * 1000000)
    .otherwise(col("price_cleaned"))
)

# Tìm giá thấp nhất
min_price = df_clean.select(min_f(col("price_vnd"))).collect()[0][0]
print(f"Giá thấp nhất: {min_price:,.0f} VND")

# Hiển thị thông tin chi tiết về nhà có giá rẻ nhất
cheapest_house = df_clean.filter(col("price_vnd") == min_price)
cheapest_house.select(
    "title", 
    "price", 
    "area", 
    "bedroom", 
    "bathroom", 
    "location",
    "url"
).show(1, False)

# Hiển thị thêm thông tin chi tiết
print("\n=== Chi tiết về bất động sản giá rẻ nhất ===")
cheapest_details = cheapest_house.select("*").collect()
if cheapest_details:
    for row in cheapest_details:
        print(f"Tiêu đề: {row['title']}")
        print(f"Giá gốc: {row['price']}")
        print(f"Giá (VND): {row['price_vnd']:,.0f}")
        print(f"Diện tích: {row['area']} m²")
        if 'bedroom' in row and row['bedroom']:
            print(f"Phòng ngủ: {row['bedroom']}")
        if 'bathroom' in row and row['bathroom']:
            print(f"Phòng tắm: {row['bathroom']}")
        print(f"Vị trí: {row['location']}")
        if 'description' in row and row['description']:
            print(f"Mô tả: {row['description'][:200]}..." if len(row['description']) > 200 else row['description'])
        if 'url' in row and row['url']:
            print(f"Link: {row['url']}")

Giá thấp nhất: 2,000,000 VND
+---------------------------------------------------------------+-------+----+-------+--------+-------------------------------------------------+------------------------------------+
|title                                                          |price  |area|bedroom|bathroom|location                                         |url                                 |
+---------------------------------------------------------------+-------+----+-------+--------+-------------------------------------------------+------------------------------------+
|Nhà gác lững Quang Châu💝phường Hoà Xuân-mới, đẹp từng centimet|2 triệu|95  |3      |2       |quang châu, Phường Hòa Xuân, Quận Cẩm Lệ, Đà Nẵng|https://nha.chotot.com/124888955.htm|
+---------------------------------------------------------------+-------+----+-------+--------+-------------------------------------------------+------------------------------------+


=== Chi tiết về bất động sản giá rẻ nhất ===
Tiêu đề: N

In [19]:
# Đường dẫn cho toàn bộ dữ liệu trong tháng 5/2025
json_path = "hdfs://namenode:9000/data/realestate/raw/chotot/house/2025/05/*"

# Đọc dữ liệu JSON từ HDFS cho toàn bộ tháng
df = spark.read.option("multiline", "false").json(json_path)
df = df.limit(5000)
# Tạo thư mục tạm nếu chưa tồn tại
import os
output_dir = "/tmp/chotot_data_may2025"
if not os.path.exists(output_dir):
    os.makedirs(output_dir)

# Lưu DataFrame thành 1 file CSV duy nhất (coalesce(1) đảm bảo chỉ có 1 file)
csv_output_path = f"{output_dir}/data.csv"
df.toPandas().to_csv(csv_output_path, index=False)

# Kiểm tra file đã được tạo chưa
print(f"File CSV đã được lưu tại: {csv_output_path}")
print(f"Kích thước file: {os.path.getsize(csv_output_path) / (1024*1024):.2f} MB")

# Tạo link tải xuống file CSV trong Jupyter
from IPython.display import HTML
import base64

def create_download_link(file_path, filename=None):
    if filename is None:
        filename = os.path.basename(file_path)
        
    with open(file_path, "rb") as f:
        data = f.read()
        
    b64 = base64.b64encode(data).decode()
    href = f'<a download="{filename}" href="data:text/csv;base64,{b64}" target="_blank">Tải xuống {filename}</a>'
    return HTML(href)

# Hiển thị link tải xuống
create_download_link(csv_output_path, "chotot_data_may2025.csv")

File CSV đã được lưu tại: /tmp/chotot_data_may2025/data.csv
Kích thước file: 4.22 MB


In [13]:
limited_df = df.limit(10000)  # Ví dụ lấy 10,000 bản ghi

# Lưu DataFrame thành CSV trong thư mục output
limited_df.coalesce(1).write.option("header", "true").mode("overwrite").csv(output_dir)

# Tìm file CSV trong thư mục (do Spark thêm phần mở rộng ngẫu nhiên)
import glob
csv_files = glob.glob(f"{output_dir}/part-*.csv")
if csv_files:
    csv_file = csv_files[0]
    print(f"File CSV tìm thấy: {csv_file}")
    
    # Tạo link tải xuống
    create_download_link(csv_file, "chotot_data_sample.csv")
else:
    print(f"Không tìm thấy file CSV trong thư mục {output_dir}")

Không tìm thấy file CSV trong thư mục /tmp/chotot_data_may2025


In [3]:
json_path = "hdfs://namenode:9000/data/realestate/raw/batdongsan/house/2025/05"

# Đọc dữ liệu JSON từ HDFS
df = spark.read.option("multiline", "false").json(json_path)

# Hiển thị schema
df.printSchema()

root
 |-- area: string (nullable = true)
 |-- bathroom: string (nullable = true)
 |-- bedroom: string (nullable = true)
 |-- crawl_timestamp: string (nullable = true)
 |-- data_type: string (nullable = true)
 |-- description: string (nullable = true)
 |-- facade_width: string (nullable = true)
 |-- floor_count: string (nullable = true)
 |-- house_direction: string (nullable = true)
 |-- interior: string (nullable = true)
 |-- latitude: string (nullable = true)
 |-- legal_status: string (nullable = true)
 |-- location: string (nullable = true)
 |-- longitude: string (nullable = true)
 |-- posted_date: string (nullable = true)
 |-- price: string (nullable = true)
 |-- price_per_m2: string (nullable = true)
 |-- road_width: string (nullable = true)
 |-- seller_info: string (nullable = true)
 |-- source: string (nullable = true)
 |-- title: string (nullable = true)
 |-- url: string (nullable = true)



25/05/23 13:02:31 WARN StandaloneAppClient$ClientEndpoint: Connection to 4649cfa041be:7077 failed; waiting for master to reconnect...
25/05/23 13:02:31 WARN StandaloneSchedulerBackend: Disconnected from Spark cluster! Waiting for reconnection...
25/05/23 13:02:46 ERROR TaskSchedulerImpl: Lost executor 0 on 172.23.0.6: Remote RPC client disassociated. Likely due to containers exceeding thresholds, or network issues. Check driver logs for WARN messages.


In [11]:
object_count = df.count()

print(f"Số lượng object JSON: {object_count}")

Số lượng object JSON: 24500


In [12]:
# Lấy dòng đầu tiên (dạng Row object)
first_row = df.first()

# In toàn bộ thông tin của dòng đầu tiên
print(first_row)

Row(area='80', bathroom='1', bedroom='1', crawl_timestamp='1747838376', data_type='house', description='Nhà mặt tiền đường kinh doanh sầm uất, khu vực dân cư đông đúc, sang trọng, an ninh, thuận tiện kinh doanh mua bán nhiều nghề hoặc cho thuê, xung quanh còn có đầy đủ các tiện ích như TTTM Aeon Mall, bệnh viện quốc tế CIH, ngân hàng, chợ, trường học các cấp, rất thuận tiện cho các sinh hoạt hằng ngày. - Vị trí: MT đường Số 2 CX Rada, P.13, Q.6 - Diện tích: 4 x 20m. - Kết cấu: Cấp 4 - Hướng: Tây - Nam - Giá: 8.8 tỷ.', floor_count='', house_direction='8', house_type=None, interior='4', latitude='10.751096', legal_status='1', length=None, living_size=None, location='Đường số 2, Phường 13, Quận 6, Tp Hồ Chí Minh', longitude='106.62455', posted_date='1747831703', price='8,8 tỷ', price_per_m2='110', seller_info="{'name': 'Minh Thanh', 'account_id': '2326347'}", source='chotot', title='Nhà MT đường số 2 Cư xá Rada Q6 dt 80m2 giá 8.8 tỷ', url='https://nha.chotot.com/121332310.htm', width=None

In [13]:
# Đếm tổng số dòng
total_count = df.count()

# Đếm số dòng sau khi loại bỏ trùng
distinct_count = df.distinct().count()

print(f"Tổng số dòng: {total_count}")
print(f"Số dòng không trùng: {distinct_count}")
print(f"Số dòng trùng lặp: {total_count - distinct_count}")

Tổng số dòng: 24500
Số dòng không trùng: 24500
Số dòng trùng lặp: 0


In [14]:
spark.stop()
